# Goal of this notebook

Develop a training loop for finetuning ASR models using TTS loss by recreating RL training found in RL4LMs/rl4lms/envs/text_generation/training_utils.py

# automatic reloading magic

# imports

In [40]:
import torch
from typing import List, Dict, Tuple, Any
import hyperpyyaml
from tqdm import tqdm
from torchaudio.models.decoder import ctc_decoder
from torch.nn.functional import softmax
import random
from jiwer import cer
import numpy as np
import speechbrain as sb
from IPython.display import Audio

## check if gpu available

In [41]:
# print hostname to make sure we are on correct node
import socket
print(socket.gethostname())

strickland.inf.ed.ac.uk


In [42]:
torch.cuda.is_available()

True

In [43]:
import os
os.getcwd()

'/disk/nfs/ostrom/s1785140/rlspeller'

# HPARAMS

In [44]:
hparams = {
    "softdtw_temp": 0.01,
    "softdtw_bandwidth": 120,
    "dist_func": "l1",
    "sentencepiece_model_path": "/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/0_char.model",
    'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain.yaml',
    'sample_rate': 16000,
}

# TOKENIZER

In [45]:
# load pretrained tokenizer used to tokenizer ASR training inputs 
import sentencepiece as spm 
spm_path = hparams["sentencepiece_model_path"]
sp = spm.SentencePieceProcessor()
sp.load(spm_path)
print(sp.vocab_size())

28


In [46]:
# test tokenizer
s = "hello world my name is jason"
# TODO pass string through text cleaners? 
encoded = sp.EncodeAsIds(s)
assert 0 not in encoded, "tried to encode an unknown character"
print(" ".join(str(idx) for idx in encoded))

1 10 2 12 12 4 1 17 4 9 12 11 1 16 20 1 6 5 16 2 1 7 8 1 26 5 8 4 6


In [47]:
sp.DecodeIds(encoded)

'hello world my name is jason'

# NEW! SIMPLE TOKENIZER

In [48]:
from speechbrain.tokenizers.SimpleTokenizer import SimpleTokenizer

In [49]:
tokenizer = SimpleTokenizer()

In [50]:
text = "hello my name is jason"
text = text.replace(' ', '|')
print(text)
ids = tokenizer.encode_as_ids(text)
ids

hello|my|name|is|jason


[9, 6, 13, 13, 16, 1, 14, 26, 1, 15, 2, 14, 6, 1, 10, 20, 1, 11, 2, 20, 16, 15]

In [51]:
tokenizer.decode_ids(ids)

'hello|my|name|is|jason'

## test simple tokenizer with probability distribution, and see if CTC decoder successfully generates n-best lists

In [52]:
# create empty array of correct dimensions
min_len, max_len = 50, 100
bsz = 4
lens = torch.randint(min_len, max_len, (bsz,))
vocab_size = len(tokenizer.vocab)

# randomly assign probaility distribution to each timestep

# try to decode

In [53]:
randn = torch.randn(bsz, max_len, vocab_size)

In [54]:
ctc_probs = softmax(randn, dim=1)
# ctc_probs

In [55]:
ctc_beamsearch_decoder_test = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=tokenizer.vocab,
    nbest=2,
    blank_token='-',
    sil_token="|",
)

predicted_ids = ctc_beamsearch_decoder_test(ctc_probs, lens)

predicted_words = []
for i, hyps in enumerate(predicted_ids):
    for j, hyp in enumerate(hyps):
        words = tokenizer.decode_ids(hyp.tokens.tolist()).split(" ")
        tup = (f"sample {i+1}, hyp {j+1}/{len(hyps)}", words)
        predicted_words.append(tup)
        print(tup)

('sample 1, hyp 1/2', ['|qzbycwmceyodq|owldldoxutazlrhgsfgzs|ga|cynkhiphfgifocrxpuoklers|xjiorv|'])
('sample 1, hyp 2/2', ['|qzbycwmceyodq|owldldoxutanlrhgsfgzs|ga|cynkhiphfgifocrxpuoklers|xjiorv|'])
('sample 2, hyp 1/2', ['|udhbjqpaoeiznrlgou|rjuzdsgpsypqkubmlwnfxfzy|ahb|jrpogqzvarftkvnyeglvhduqbeong|l|tdaedsfh|'])
('sample 2, hyp 2/2', ['|udhbjqpaoeiznrlgou|rjuzdsgpsypqkubmlwnfxfzy|ahb|jrpogqzvacftkvnyeglvhduqbeong|l|tdaedsfh|'])
('sample 3, hyp 1/2', ['|dkjeyig|n|zkcijufsxfrvrupdhewqnxmjeolmwoesqcaiguhrfjreblxglidvzsqjcntztsjmpkvvfjksxzobpmsd|'])
('sample 3, hyp 2/2', ['|dkjeyig|n|zkcijufsxfrvrupdhewqnxmjeolwoesqcaiguhrfjreblxglidvzsqjcntztsjmpkvvfjksxzobpmsd|'])
('sample 4, hyp 1/2', ['|kdztaujcuarxadqfsqri|iwonwxvgushivzrvolorydsklnjvspuapxqudsjbqrhjrjrhckptzcykozdepuqr|'])
('sample 4, hyp 2/2', ['|keztaujcuarxadqfsqri|iwonwxvgushivzrvolorydsklnjvspuapxqudsjbqrhjrjrhckptzcykozdepuqr|'])


# LOAD ASR (PRETRAINED)

In [56]:
from templates.speech_recognition_CharTokens_NoLM.ASR.train import ASR
from templates.speech_recognition_CharTokens_NoLM.ASR.train import dataio_prepare
from torch.utils.data import DataLoader
from speechbrain.dataio.dataloader import LoopedLoader

In [57]:
# Load hyperparameters file with command-line overrides
speechbrain_hparams_file = hparams['speechbrain_hparams_file']
with open(speechbrain_hparams_file) as f:
    speechbrain_hparams = hyperpyyaml.load_hyperpyyaml(f)

/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/rirs_noises.zip exists. Skipping download


In [58]:
speechbrain_hparams['save_folder']

'/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/ASR/results/CRDNN_CHAR_LJSpeech_halved/2602/save'

In [59]:
# initialise trainer (we don't want to train, but model is tightly coupled with trainer)
asr_brain = ASR(
    modules=speechbrain_hparams["modules"],
    opt_class=speechbrain_hparams["opt_class"],
    hparams=speechbrain_hparams,
    checkpointer=speechbrain_hparams["checkpointer"],
)

def setup_asr_brain_for_infer(asr_brain):
    asr_brain.on_evaluate_start(min_key="WER") # We call the on_evaluate_start that will load the best model
    asr_brain.modules.eval() # We set the model to eval mode (remove dropout etc)

print("if on_evaluate_start() get runtime error, likely need to restart notebook kernel")
setup_asr_brain_for_infer(asr_brain)

if on_evaluate_start() get runtime error, likely need to restart notebook kernel


In [60]:
# create dataset and dataloader for inference
datasets = dataio_prepare(speechbrain_hparams)

test_set = datasets['test']

if not isinstance(test_set, DataLoader) or isinstance(test_set, LoopedLoader):
    test_loader_kwargs=speechbrain_hparams["test_dataloader_opts"]
    test_set = asr_brain.make_dataloader(
        test_set, stage=sb.Stage.TEST, **test_loader_kwargs
    )

In [61]:
# get vocab from tokenizer (needed for ctc decoding)
vocab_size = len(asr_brain.hparams.tokenizer)
vocab = []
for i in range(vocab_size):
    vocab.append(asr_brain.hparams.tokenizer.decode_ids([i]))
print(vocab)

# edit vocab to match default ctc decoder symbols for blank and silence
vocab[0] = '-'
vocab[1] = "|"

print(vocab)

[' ⁇ ', '', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']
['-', '|', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']


In [62]:
ctc_beamsearch_decoder = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=vocab,
    nbest=100,
    blank_token='-',
    sil_token="|",
)

In [64]:
# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, greedy=False, num_batches_to_transcribe=None):
    # Now we iterate over the dataset and we simply compute_forward and decode
    with torch.no_grad():
        transcripts = []
        for batch in tqdm(list(dataset)[:num_batches_to_transcribe], dynamic_ncols=True):
            orig_transcriptions = batch.words

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            if greedy:
                predicted_ids = sb.decoders.ctc_greedy_decode(
                    predictions["ctc_logprobs"], asr_brain.feat_lens, blank_id=asr_brain.hparams.blank_index
                )
                predicted_words = [
                    asr_brain.tokenizer.decode_ids(ids).split(" ")
                    for ids in predicted_ids
                ]
            else:
                # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
                batch_max_len = predictions["ctc_logprobs"].size(1)
                bsz = predictions["ctc_logprobs"].size(0)
                mel_lens = torch.zeros(bsz)
                for i, len_ratio in enumerate(asr_brain.feat_lens):
                    mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
                
                predicted_ids = ctc_beamsearch_decoder(
                    predictions["ctc_logprobs"], lengths=mel_lens
                )

                predicted_words = []
                for i, (utt_id, orig_text, hyps) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids)):
                    print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                    sample_cers = []
                    for j, hyp in enumerate(hyps):
                        words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        # words = tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        hyp_cer = 100 * cer(orig_text, words)
                        sample_cers.append(hyp_cer)
                        print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                        predicted_words.append((f"sample {i+1}, hyp {j+1}/{len(hyps)}", words))
                        
                    print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

            transcripts.append(predicted_words)

    return transcripts, ctc_probs

# transcripts, ctc_probs = transcribe_dataset(asr_brain, test_set, greedy=False, num_batches_to_transcribe=1)

# LOAD WORD ALIGNED WAVS into dataset

In [65]:
# imitate CLAs
import sys
import argparse
import math
import glob
from tqdm import tqdm

In [66]:
# set these in yaml config!
train_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
valid_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
test_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [67]:
speechbrain_hparams['train_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
speechbrain_hparams['valid_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
speechbrain_hparams['test_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [68]:
def dataio_prepare(hparams):
    """This function prepares the datasets to be used in the brain class.
    It also defines the data processing pipeline through user-defined functions.


    Arguments
    ---------
    hparams : dict
        This dictionary is loaded from the `train.yaml` file, and it includes
        all the hyperparameters needed for dataset construction and loading.

    Returns
    -------
    datasets : dict
        Dictionary containing "train", "valid", and "test" keys that correspond
        to the DynamicItemDataset objects.
    """
    # Define audio pipeline. In this case, we simply read the path contained
    # in the variable wav with the audio reader.
    # wav path like: data/ljspeech_wavs_16khz_word_aligned/differs/differs__LJ001-0001__occ1__len8320.wav
    @sb.utils.data_pipeline.takes("wav")
    @sb.utils.data_pipeline.provides("sig", "wav_path", "utt_id")
    def audio_pipeline(wav_path):
        """Load the audio signal. This is done on the CPU in the `collate_fn`."""
        sig = sb.dataio.dataio.read_audio(wav_path)
        yield sig

        yield wav_path

        utt_id = wav_path.split("/")[-1].split(".")[0]
        yield utt_id

    @sb.utils.data_pipeline.takes("samples_to_graphemes_ratio")
    @sb.utils.data_pipeline.provides("samples_to_graphemes_ratio")
    def ratio_pipeline(samples_to_graphemes_ratio):
        yield samples_to_graphemes_ratio

    @sb.utils.data_pipeline.takes("length")
    @sb.utils.data_pipeline.provides("length")
    def length_pipeline(length):
        yield length

    @sb.utils.data_pipeline.takes("words")
    @sb.utils.data_pipeline.provides("words")
    def text_pipeline(words):
        """Processes the transcriptions to generate proper labels

        NB Make sure that you yield exactly what is defined above in @sb.utils.data_pipeline.provides()"""
        yield words

        # TODO also yield mel for calculating fastpitch softdtw loss

    # Define datasets from json data manifest file
    # Define datasets sorted by ascending lengths for efficiency
    datasets = {}
    data_info = {
        "train": hparams["train_annotation"],
        "valid": hparams["valid_annotation"],
        "test": hparams["test_annotation"],
    }

    for split in data_info:
        datasets[split] = sb.dataio.dataset.DynamicItemDataset.from_json(
            json_path=data_info[split],
            dynamic_items=[audio_pipeline, ratio_pipeline, length_pipeline, text_pipeline],
            output_keys=[
                "id",
                "sig",
                "wav_path",
                "utt_id",
                "samples_to_graphemes_ratio",
                "length",
                "words",
            ],
        )
        hparams[f"{split}_dataloader_opts"]["shuffle"] = True

    # TODO uncomment this!!!

    # # Sorting training data with ascending order makes the code  much
    # # faster  because we minimize zero-padding. In most of the cases, this
    # # does not harm the performance.
    # if hparams["sorting"] == "ascending":
    #     datasets["train"] = datasets["train"].filtered_sorted(sort_key="length")
    #     hparams["train_dataloader_opts"]["shuffle"] = False

    # elif hparams["sorting"] == "descending":
    #     datasets["train"] = datasets["train"].filtered_sorted(
    #         sort_key="length", reverse=True
    #     )
    #     hparams["train_dataloader_opts"]["shuffle"] = False

    # elif hparams["sorting"] == "random":
    #     hparams["train_dataloader_opts"]["shuffle"] = True
    #     pass

    # else:
    #     raise NotImplementedError(
    #         "sorting must be random, ascending or descending"
    #     )
    
    return datasets

datasets = dataio_prepare(speechbrain_hparams)

In [69]:
# convert from datasets to dataloaders
split2stage = {"train": sb.Stage.TRAIN, "valid": sb.Stage.VALID, "test": sb.Stage.TEST}
for split in ["train", "valid", "test"]:
    if not isinstance(datasets[split], DataLoader) or isinstance(datasets[split], LoopedLoader):
        dataloader_kwargs=speechbrain_hparams[f"{split}_dataloader_opts"]
        datasets[split] = asr_brain.make_dataloader(
            datasets[split], stage=split2stage[split], **dataloader_kwargs
        )

In [70]:
def set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|"):
    """ctc_probs [bsz, max_seq_len, vocab_size]"""
    new_probability = -math.inf if log_probs else 0.0
    whitespace_index = vocab.index(whitespace_symbol)
    ctc_probs[:,:,whitespace_index] = new_probability
    return ctc_probs

In [73]:
# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, 
                       num_batches_to_transcribe=None,
                       hack_whitespace_probs=False, collapse_whitespace=True,
                       print_info=False):
    # Now we iterate over the dataset and we simply compute_forward and decode

    orig_words = []
    printouts = []
    orig_wavs = []
    n = 0 # number of batches transcribed

    with torch.no_grad():
        for batch in tqdm(dataset, dynamic_ncols=True, total=num_batches_to_transcribe):
            # break out of loop if we have transcribed enough batches
            if n >= num_batches_to_transcribe:
                break
            n += 1

            orig_transcriptions = batch.words
            wavs = batch.sig.data

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            # hack probabilities to set all probs to 0 for whitespace
            if hack_whitespace_probs:
                ctc_probs = set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|")

            # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
            batch_max_len = predictions["ctc_logprobs"].size(1)
            bsz = predictions["ctc_logprobs"].size(0)
            mel_lens = torch.zeros(bsz)
            for i, len_ratio in enumerate(asr_brain.feat_lens):
                mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
            
            predicted_ids = ctc_beamsearch_decoder(
                predictions["ctc_logprobs"], lengths=mel_lens
            )

            # iterate over samples in batch
            for i, (utt_id, orig_text, hyps, wav) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids, wavs)):
                sample_printout = f"\nsample {i+1} - ({utt_id}: '{orig_text}')"
                # if print_info: print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                sample_cers = []
                for j, hyp in enumerate(hyps):
                    words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist())
                    if collapse_whitespace:
                        words = "".join(c for c in words if c != " ")
                    hyp_cer = 100 * cer(orig_text, words)
                    sample_cers.append(hyp_cer)
                    sample_printout += f"\n\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'"
                    # if print_info: print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                    
                sample_printout += f"\n\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ==="
                # if print_info: print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

                orig_words.append(orig_text)
                printouts.append(sample_printout)
                orig_wavs.append(wav)

    output_dict = {
        "words": orig_words,
        "wavs": orig_wavs,
        "printouts": printouts,
    }

    return output_dict

transcription_output_dict = transcribe_dataset(asr_brain, datasets["train"], 
                                               num_batches_to_transcribe=10,
                                               collapse_whitespace=False)

  0%|                                                                            | 0/10 [00:00<?, ?it/s]

DEBUG INSIDE PREPARE FEATURES, feats.shape=torch.Size([20, 94, 40]) wav_lens.shape=torch.Size([20])


 10%|██████▊                                                             | 1/10 [00:02<00:26,  2.93s/it]

DEBUG INSIDE PREPARE FEATURES, feats.shape=torch.Size([20, 109, 40]) wav_lens.shape=torch.Size([20])


 20%|█████████████▌                                                      | 2/10 [00:06<00:25,  3.13s/it]

...

 80%|██████████████████████████████████████████████████████▍             | 8/10 [00:23<00:05,  2.87s/it]

DEBUG INSIDE PREPARE FEATURES, feats.shape=torch.Size([20, 88, 40]) wav_lens.shape=torch.Size([20])


 90%|█████████████████████████████████████████████████████████████▏      | 9/10 [00:25<00:02,  2.81s/it]

DEBUG INSIDE PREPARE FEATURES, feats.shape=torch.Size([20, 110, 40]) wav_lens.shape=torch.Size([20])


100%|███████████████████████████████████████████████████████████████████| 10/10 [00:29<00:00,  2.92s/it]


In [74]:
# display printouts and create audio player for each sample
for printout, wav in zip(transcription_output_dict["printouts"], transcription_output_dict["wavs"]):
    print(printout)
    display(Audio(wav, rate=16000))


sample 1 - (offering__LJ044-0102__occ1__len8000: 'offering')
	hyp 1/47 (CER=12.5%): 'offerin '
	hyp 2/47 (CER=25.0%): 'offeri '
	hyp 3/47 (CER=25.0%): 'offern '
	hyp 4/47 (CER=25.0%): 'offeren '
	hyp 5/47 (CER=25.0%): 'offein '
	hyp 6/47 (CER=25.0%): 'ofterin '
	hyp 7/47 (CER=25.0%): 'oferin '
	hyp 8/47 (CER=25.0%): 'fferin '
	hyp 9/47 (CER=25.0%): 'offerie '
	hyp 10/47 (CER=37.5%): 'offerei '
	hyp 11/47 (CER=25.0%): 'afferin '
	hyp 12/47 (CER=37.5%): 'offei '
	hyp 13/47 (CER=37.5%): 'offen '
	hyp 14/47 (CER=37.5%): 'ofteri '
	hyp 15/47 (CER=25.0%): 'offrin '
	hyp 16/47 (CER=37.5%): 'oferi '
	hyp 17/47 (CER=25.0%): 'oufferin '
	hyp 18/47 (CER=37.5%): 'fferi '
	hyp 19/47 (CER=25.0%): 'offeriy '
	hyp 20/47 (CER=37.5%): 'oftern '
	hyp 21/47 (CER=37.5%): 'ofteren '
	hyp 22/47 (CER=37.5%): 'oftein '
	hyp 23/47 (CER=37.5%): 'ofern '
	hyp 24/47 (CER=37.5%): 'ffern '
	hyp 25/47 (CER=37.5%): 'oferen '
	hyp 26/47 (CER=37.5%): 'fferen '
	hyp 27/47 (CER=25.0%): 'offer n '
	hyp 28/47 (CER=37.5%): 


sample 2 - (fished__LJ002-0203__occ1__len7200: 'fished')
	hyp 1/48 (CER=33.3%): 'fish '
	hyp 2/48 (CER=50.0%): 'ffish '
	hyp 3/48 (CER=66.7%): 'o fish '
	hyp 4/48 (CER=50.0%): 'ofish '
	hyp 5/48 (CER=50.0%): 'fifsh '
	hyp 6/48 (CER=66.7%): 'f fish '
	hyp 7/48 (CER=50.0%): 'fisch '
	hyp 8/48 (CER=66.7%): 't fish '
	hyp 9/48 (CER=66.7%): 'u fish '
	hyp 10/48 (CER=50.0%): 'ufish '
	hyp 11/48 (CER=50.0%): 'fisih '
	hyp 12/48 (CER=50.0%): 'fisfh '
	hyp 13/48 (CER=50.0%): 'fiscsh '
	hyp 14/48 (CER=50.0%): 'fsh '
	hyp 15/48 (CER=66.7%): 'offish '
	hyp 16/48 (CER=66.7%): 'ffifsh '
	hyp 17/48 (CER=33.3%): 'fishs '
	hyp 18/48 (CER=16.7%): 'fishe '
	hyp 19/48 (CER=33.3%): 'fishi '
	hyp 20/48 (CER=83.3%): 'o fifsh '
	hyp 21/48 (CER=50.0%): 'fisfsh '
	hyp 22/48 (CER=66.7%): 'ofifsh '
	hyp 23/48 (CER=50.0%): 'efish '
	hyp 24/48 (CER=50.0%): 'ish '
	hyp 25/48 (CER=66.7%): 'h fish '
	hyp 26/48 (CER=83.3%): 'f fifsh '
	hyp 27/48 (CER=50.0%): 'hfish '
	hyp 28/48 (CER=66.7%): 'ffisch '
	hyp 29/48 (CER=5


sample 3 - (reproductive__LJ026-0024__occ1__len9760: 'reproductive')
	hyp 1/48 (CER=33.3%): 're product '
	hyp 2/48 (CER=41.7%): 're croduct '
	hyp 3/48 (CER=41.7%): 're prduct '
	hyp 4/48 (CER=50.0%): 're crduct '
	hyp 5/48 (CER=41.7%): 're produpt '
	hyp 6/48 (CER=41.7%): 're poroduct '
	hyp 7/48 (CER=50.0%): 're crodupt '
	hyp 8/48 (CER=50.0%): 're coroduct '
	hyp 9/48 (CER=41.7%): 're produt '
	hyp 10/48 (CER=41.7%): 're puroduct '
	hyp 11/48 (CER=50.0%): 're crodut '
	hyp 12/48 (CER=50.0%): 're curoduct '
	hyp 13/48 (CER=41.7%): 're preoduct '
	hyp 14/48 (CER=41.7%): 're produc '
	hyp 15/48 (CER=41.7%): 're prodouct '
	hyp 16/48 (CER=50.0%): 're creoduct '
	hyp 17/48 (CER=50.0%): 're croduc '
	hyp 18/48 (CER=25.0%): 'reproduct '
	hyp 19/48 (CER=50.0%): 're crodouct '
	hyp 20/48 (CER=50.0%): 'n re product '
	hyp 21/48 (CER=33.3%): 'recroduct '
	hyp 22/48 (CER=41.7%): 're prorduct '
	hyp 23/48 (CER=33.3%): 'recproduct '
	hyp 24/48 (CER=50.0%): 'a re product '
	hyp 25/48 (CER=58.3%)


sample 4 - (englishmen__LJ017-0213__occ1__len9760: 'englishmen')
	hyp 1/50 (CER=20.0%): 'engishme '
	hyp 2/50 (CER=20.0%): 'enguishme '
	hyp 3/50 (CER=10.0%): 'englishme '
	hyp 4/50 (CER=30.0%): 'egishme '
	hyp 5/50 (CER=30.0%): 'engishmi '
	hyp 6/50 (CER=30.0%): 'angishme '
	hyp 7/50 (CER=30.0%): 'engishma '
	hyp 8/50 (CER=30.0%): 'eguishme '
	hyp 9/50 (CER=30.0%): 'enguishmi '
	hyp 10/50 (CER=30.0%): 'anguishme '
	hyp 11/50 (CER=20.0%): 'engluishme '
	hyp 12/50 (CER=20.0%): 'eglishme '
	hyp 13/50 (CER=20.0%): 'englishmi '
	hyp 14/50 (CER=30.0%): 'enguishma '
	hyp 15/50 (CER=20.0%): 'anglishme '
	hyp 16/50 (CER=30.0%): 'engushme '
	hyp 17/50 (CER=40.0%): 'a engishme '
	hyp 18/50 (CER=20.0%): 'englishma '
	hyp 19/50 (CER=20.0%): 'englshme '
	hyp 20/50 (CER=40.0%): 't engishme '
	hyp 21/50 (CER=30.0%): 'engiushme '
	hyp 22/50 (CER=20.0%): 'engdishme '
	hyp 23/50 (CER=40.0%): 'a enguishme '
	hyp 24/50 (CER=40.0%): 'r engishme '
	hyp 25/50 (CER=30.0%): 'engishmo '
	hyp 26/50 (CER=30.0%):


sample 5 - (youths__LJ003-0094__occ1__len8320: 'youths')
	hyp 1/48 (CER=16.7%): 'youth '
	hyp 2/48 (CER=33.3%): 'yuth '
	hyp 3/48 (CER=33.3%): 'outh '
	hyp 4/48 (CER=33.3%): 'youteh '
	hyp 5/48 (CER=50.0%): 'uth '
	hyp 6/48 (CER=0.0%): 'youths '
	hyp 7/48 (CER=33.3%): 'uouth '
	hyp 8/48 (CER=16.7%): 'youth '
	hyp 9/48 (CER=50.0%): 'yuteh '
	hyp 10/48 (CER=33.3%): 'y outh '
	hyp 11/48 (CER=33.3%): 'yeuth '
	hyp 12/48 (CER=50.0%): 'outeh '
	hyp 13/48 (CER=16.7%): 'yuths '
	hyp 14/48 (CER=33.3%): 'yout '
	hyp 15/48 (CER=16.7%): 'ouths '
	hyp 16/48 (CER=50.0%): 'a youth '
	hyp 17/48 (CER=33.3%): 'yuth '
	hyp 18/48 (CER=33.3%): 'outh '
	hyp 19/48 (CER=33.3%): 'y uth '
	hyp 20/48 (CER=33.3%): 'youtdh '
	hyp 21/48 (CER=50.0%): 't youth '
	hyp 22/48 (CER=66.7%): 'uteh '
	hyp 23/48 (CER=50.0%): 'yut '
	hyp 24/48 (CER=50.0%): 'n youth '
	hyp 25/48 (CER=50.0%): 'euth '
	hyp 26/48 (CER=33.3%): 'outh '
	hyp 27/48 (CER=16.7%): 'youtehs '
	hyp 28/48 (CER=33.3%): 'uths '
	hyp 29/48 (CER=50.0%): 'out 

...


sample 16 - (atmospheric__LJ025-0176__occ1__len11360: 'atmospheric')
	hyp 1/50 (CER=63.6%): 'tat misfirc '
	hyp 2/50 (CER=54.5%): 'tat mispirc '
	hyp 3/50 (CER=54.5%): 'tat mosfirc '
	hyp 4/50 (CER=45.5%): 'tat mospirc '
	hyp 5/50 (CER=72.7%): 'that misfirc '
	hyp 6/50 (CER=54.5%): 'tat misfiric '
	hyp 7/50 (CER=63.6%): 'that mispirc '
	hyp 8/50 (CER=63.6%): 'that mosfirc '
	hyp 9/50 (CER=45.5%): 'tat mispiric '
	hyp 10/50 (CER=45.5%): 'tat mosfiric '
	hyp 11/50 (CER=54.5%): 'that mospirc '
	hyp 12/50 (CER=36.4%): 'tat mospiric '
	hyp 13/50 (CER=63.6%): 'that misfiric '
	hyp 14/50 (CER=63.6%): 'tat mhsfirc '
	hyp 15/50 (CER=63.6%): 'tat masfirc '
	hyp 16/50 (CER=54.5%): 'that mispiric '
	hyp 17/50 (CER=63.6%): 'tat missfirc '
	hyp 18/50 (CER=54.5%): 'tat mhspirc '
	hyp 19/50 (CER=54.5%): 'that mosfiric '
	hyp 20/50 (CER=72.7%): 'tat mis sfirc '
	hyp 21/50 (CER=54.5%): 'tat maspirc '
	hyp 22/50 (CER=63.6%): 'tat mysfirc '
	hyp 23/50 (CER=63.6%): 'tat misspirc '
	hyp 24/50 (CER=45.5%): 


sample 17 - (metamorphosis__LJ025-0119__occ1__len17440: 'metamorphosis')
	hyp 1/49 (CER=46.2%): 'met morfasess '
	hyp 2/49 (CER=53.8%): 'mett morfasess '
	hyp 3/49 (CER=38.5%): 'met morfases '
	hyp 4/49 (CER=46.2%): 'mett morfases '
	hyp 5/49 (CER=53.8%): 'met morfascess '
	hyp 6/49 (CER=46.2%): 'met morfassess '
	hyp 7/49 (CER=61.5%): 'mett morfascess '
	hyp 8/49 (CER=53.8%): 'mett morfassess '
	hyp 9/49 (CER=46.2%): 'met morfasces '
	hyp 10/49 (CER=38.5%): 'met morfasses '
	hyp 11/49 (CER=38.5%): 'met morfaess '
	hyp 12/49 (CER=53.8%): 'mett morfasces '
	hyp 13/49 (CER=53.8%): 'meto morfasess '
	hyp 14/49 (CER=46.2%): 'mett morfasses '
	hyp 15/49 (CER=46.2%): 'mett morfaess '
	hyp 16/49 (CER=46.2%): 'met morfaes '
	hyp 17/49 (CER=38.5%): 'met morfosess '
	hyp 18/49 (CER=61.5%): 'metto morfasess '
	hyp 19/49 (CER=38.5%): 'met morasess '
	hyp 20/49 (CER=46.2%): 'meto morfases '
	hyp 21/49 (CER=46.2%): 'met morfacess '
	hyp 22/49 (CER=53.8%): 'met morfascsess '
	hyp 23/49 (CER=53.8%): 


sample 18 - (unsound__LJ010-0232__occ1__len12320: 'unsound')
	hyp 1/50 (CER=0.0%): 'unsound '
	hyp 2/50 (CER=14.3%): 'uonsound '
	hyp 3/50 (CER=14.3%): 'un sound '
	hyp 4/50 (CER=0.0%): 'unsound '
	hyp 5/50 (CER=28.6%): 'uon sound '
	hyp 6/50 (CER=14.3%): 'ounsound '
	hyp 7/50 (CER=28.6%): 'a unsound '
	hyp 8/50 (CER=14.3%): 'unound '
	hyp 9/50 (CER=14.3%): 'uonsound '
	hyp 10/50 (CER=14.3%): 'un sound '
	hyp 11/50 (CER=28.6%): 'e unsound '
	hyp 12/50 (CER=28.6%): 'u unsound '
	hyp 13/50 (CER=14.3%): 'onsound '
	hyp 14/50 (CER=28.6%): 'oun sound '
	hyp 15/50 (CER=28.6%): 'w unsound '
	hyp 16/50 (CER=14.3%): 'unssound '
	hyp 17/50 (CER=28.6%): 'o unsound '
	hyp 18/50 (CER=28.6%): 'l unsound '
	hyp 19/50 (CER=42.9%): 'a uonsound '
	hyp 20/50 (CER=42.9%): 'a un sound '
	hyp 21/50 (CER=28.6%): 's unsound '
	hyp 22/50 (CER=28.6%): 'g unsound '
	hyp 23/50 (CER=28.6%): 'uonound '
	hyp 24/50 (CER=14.3%): 'un ound '
	hyp 25/50 (CER=28.6%): 'uon sound '
	hyp 26/50 (CER=28.6%): 'n unsound '
	hyp


sample 19 - (backing__LJ015-0032__occ1__len7040: 'backing')
	hyp 1/50 (CER=0.0%): 'backing '
	hyp 2/50 (CER=14.3%): 'tbacking '
	hyp 3/50 (CER=14.3%): 'backin '
	hyp 4/50 (CER=14.3%): 'dbacking '
	hyp 5/50 (CER=14.3%): 'nbacking '
	hyp 6/50 (CER=28.6%): 't backing '
	hyp 7/50 (CER=28.6%): 'n backing '
	hyp 8/50 (CER=28.6%): 'i backing '
	hyp 9/50 (CER=28.6%): 'tbackin '
	hyp 10/50 (CER=14.3%): 'backig '
	hyp 11/50 (CER=28.6%): 'd backing '
	hyp 12/50 (CER=14.3%): 'hbacking '
	hyp 13/50 (CER=14.3%): 'becking '
	hyp 14/50 (CER=28.6%): 'a backing '
	hyp 15/50 (CER=28.6%): 'o backing '
	hyp 16/50 (CER=14.3%): 'backng '
	hyp 17/50 (CER=28.6%): 'h backing '
	hyp 18/50 (CER=14.3%): 'ibacking '
	hyp 19/50 (CER=28.6%): 'dbackin '
	hyp 20/50 (CER=14.3%): 'bhcking '
	hyp 21/50 (CER=14.3%): 'lbacking '
	hyp 22/50 (CER=28.6%): 'nbackin '
	hyp 23/50 (CER=28.6%): 'ntbacking '
	hyp 24/50 (CER=0.0%): 'backing '
	hyp 25/50 (CER=14.3%): 'wbacking '
	hyp 26/50 (CER=14.3%): 'bcking '
	hyp 27/50 (CER=42.9%


sample 20 - (matron__LJ006-0290__occ1__len9760: 'matron')
	hyp 1/50 (CER=33.3%): 'ma trin '
	hyp 2/50 (CER=16.7%): 'matrin '
	hyp 3/50 (CER=50.0%): 'ma trien '
	hyp 4/50 (CER=33.3%): 'matrien '
	hyp 5/50 (CER=50.0%): 'ma trian '
	hyp 6/50 (CER=33.3%): 'matrian '
	hyp 7/50 (CER=33.3%): 'ma tren '
	hyp 8/50 (CER=16.7%): 'matren '
	hyp 9/50 (CER=50.0%): 'may trin '
	hyp 10/50 (CER=33.3%): 'maytrin '
	hyp 11/50 (CER=66.7%): 'may trien '
	hyp 12/50 (CER=50.0%): 'maytrien '
	hyp 13/50 (CER=50.0%): 'mat trin '
	hyp 14/50 (CER=66.7%): 'mat trien '
	hyp 15/50 (CER=50.0%): 'ma trein '
	hyp 16/50 (CER=33.3%): 'matrein '
	hyp 17/50 (CER=33.3%): 'mattrin '
	hyp 18/50 (CER=33.3%): 'maetrin '
	hyp 19/50 (CER=50.0%): 'mattrien '
	hyp 20/50 (CER=33.3%): 'ma tran '
	hyp 21/50 (CER=50.0%): 'maetrien '
	hyp 22/50 (CER=16.7%): 'matran '
	hyp 23/50 (CER=66.7%): 'may trian '
	hyp 24/50 (CER=50.0%): 'maytrian '
	hyp 25/50 (CER=66.7%): 'mat trian '
	hyp 26/50 (CER=50.0%): 'may tren '
	hyp 27/50 (CER=33.3%): '